# Projeto final para Deep Learning
## Introdução

Escrita científica faz parte de qualquer descoberta científica. Todo pesquisador contribui a sociedade dentro de um contexto. O contexto é a literatura disponível que da suporte para a produção do novo conhecimento. Portanto a produção textual é parte essencial para a geração de novos conhecimentos, e sem referência de outros trabalhos científicos ela é uma ilha inexistênte.

Essa característica dos textos científicos nos impõe uma necessidade de ter conehcimento de referências que embasam nossa nova produção. Apesar que essa seja as obrigações de um bom cientísta - estar em dia com a literatura necessária para defender sua tese - o volume de trabalhos disponíveis é maior que nossa capacidade humana de leitura no nosso tempo de vida.

Para suprimir essa limitação nós precisamos desenvolver novas tecnologias que permita o homem produzir novo conhecimento como um novo nó na rede de literária.

O processamento de linguagem natural são os conjuntos de algorítmos que fornecem a sequencia de caractéres as propriedades linguísticas e lógica inerentes a capacidade humana de raciocinar. Nós temos a capacidade de aplicar algorítmos para segmentar texto em frases e extrair proposições lógicas apartir de frases, parágrafos e textos.

O presente trabalho pretende utilizar processamento de linguagem natural juntamente com <i> deep learning </i> para desenvolver um sistema de sugestão de referência para a frases escritas em documento digital. 

## Objetivos

<b>Gerais <br><br></b>
1. Desenvolver um sistema de sugestão de referências a partir de frases escritas em um editor de texto.

<b>Específicos <br><br></b>
1. Construir um web-crawler para adquirir artigos científicos de um determidado tema;
1. Extrair o conteúdo textual dos artigos científicos;
1. Extrair as características dos textos dos artigos científicos;
1. Construir lista com documentos contendo menor distância para uma dada frase;
1. Implementar um plugin de Vim para sugestão de referências. 


## Implementação

### Instalando dependencias

In [8]:
#!conda install -c conda-forge biopython -y

#!conda install -c conda-forge nltk -y

#!git clone https://github.com/ckreibich/scholar.py

#!conda install -c conda-forge spacy -y

Fetching package metadata ...............
Solving package specifications: .

# All requested packages already installed.
# packages in environment at /opt/conda:
#
spacy                     2.0.8                    py36_0    conda-forge


### Crawler as

In [2]:
from Bio import Entrez,Medline
import numpy as np
import json
import os
batch_size  = 2000

In [5]:
!mkdir ./data
!mkdir ./data/raw
!mkdir ./data/pdf
!mkdir ./data/tokenized

filename = lambda x: './data/raw/'+x['PMID']+'.json'

def get_pmid(term='"speed cells"'):
    from Bio import Entrez,Medline

    Entrez.email = 'dr.publico88@gmail.com'


    with Entrez.egquery(term=term) as handle:
        record       = Entrez.read(handle)
        record_count = int(''.join([entry['Count'] for entry in record['eGQueryResult'] if entry['DbName']=='pubmed']))

    with Entrez.esearch(db="pubmed", term=term, retmax=record_count) as handle:
        record = Entrez.read(handle)
        idlist = record["IdList"]
    
    return idlist


def get_json(term='speed cells'):
    term        = '"'+term+'"'
    pmid_list   = get_pmid(term)
    nof_batch   = np.ceil(len(pmid_list)/batch_size)
    
    for b in range(int(nof_batch)):
        if b < nof_batch-1:
            pmid_batch = [pmid_list[x+batch_size*b] for x in range(batch_size)]
        else:
            pmid_batch = pmid_list[batch_size*b:]

        with Entrez.efetch(db="pubmed", id=pmid_batch, rettype="medline", retmode="text") as handle:
            for record in Medline.parse(handle):
                print(record['PMID'],end=',')
                record['term'] = term.replace('"','')
                with open(filename(record),'w') as json_file:
                    json.dump(record, json_file, indent=5)
            print('\n')
        print(len(pmid_batch),end=',')

def get_scholar(jsonFilename):
    import json
    import sys
    sys.path.insert(0, './scholar.py')
    import scholar as spy
    import requests
    import re

    spy_settings = spy.ScholarSettings()
    spy_settings.citform = spy_settings.CITFORM_BIBTEX;
    spy_settings.results = 1;

    spy_querier = spy.ScholarQuerier()
    spy_querier.apply_settings(spy_settings)
    spy_query = spy.SearchScholarQuery()

    with open(jsonFilename, "r+") as jsonFile:
        

        jsonData = json.load(jsonFile)
        spy_query.set_phrase(jsonData['TI'])

        spy_querier.send_query(spy_query)

        if spy_querier.articles:
            print(jsonFilename)
            scholar_dict = spy_querier.articles[0].__dict__['attrs']
            
            for key in scholar_dict:
                if key is not 'excerpt':
                    jsonData['scholar_'+key] = scholar_dict[key]

            html=''
            for line in requests.get(jsonData['scholar_url_versions'][0]):
                html=html+str(line)

            html_href = [href.replace("'b'","") for href in re.findall('href="(.*?)"',html)]
            jsonData['scholar_pdf'] = list(set([href for href in html_href if 'pdf' in href]))

            jsonFile.seek(0)  # rewind
            json.dump(jsonData, jsonFile, indent=5)
            jsonFile.truncate()


mkdir: cannot create directory ‘./data’: File exists
mkdir: cannot create directory ‘./data/raw’: File exists
mkdir: cannot create directory ‘./data/pdf’: File exists
mkdir: cannot create directory ‘./data/tokenized’: File exists


In [ ]:
from multiprocessing import Pool
    
raw_path = '/home/jovyan/notebook/BTI/Deep/data/raw'
raw_list = [os.path.join(raw_path,raw) for raw in os.listdir(raw_path)]
p = Pool(40)
p.map(get_scholar,raw_list)

/home/jovyan/notebook/BTI/Deep/data/raw/9883739.json
/home/jovyan/notebook/BTI/Deep/data/raw/12707432.json
/home/jovyan/notebook/BTI/Deep/data/raw/18957540.json
/home/jovyan/notebook/BTI/Deep/data/raw/16361444.json
/home/jovyan/notebook/BTI/Deep/data/raw/27474226.json
/home/jovyan/notebook/BTI/Deep/data/raw/27350344.json
/home/jovyan/notebook/BTI/Deep/data/raw/29269262.json
/home/jovyan/notebook/BTI/Deep/data/raw/16790597.json
/home/jovyan/notebook/BTI/Deep/data/raw/8813348.json
/home/jovyan/notebook/BTI/Deep/data/raw/9051783.json
/home/jovyan/notebook/BTI/Deep/data/raw/2355248.json
/home/jovyan/notebook/BTI/Deep/data/raw/27042284.json
/home/jovyan/notebook/BTI/Deep/data/raw/16515845.json
/home/jovyan/notebook/BTI/Deep/data/raw/26711678.json
/home/jovyan/notebook/BTI/Deep/data/raw/22219273.json
/home/jovyan/notebook/BTI/Deep/data/raw/28028789.json
/home/jovyan/notebook/BTI/Deep/data/raw/27346750.json
/home/jovyan/notebook/BTI/Deep/data/raw/22823987.json
/home/jovyan/notebook/BTI/Deep/d

/home/jovyan/notebook/BTI/Deep/data/raw/12436422.json
/home/jovyan/notebook/BTI/Deep/data/raw/18286399.json
/home/jovyan/notebook/BTI/Deep/data/raw/24741034.json
/home/jovyan/notebook/BTI/Deep/data/raw/7498410.json
/home/jovyan/notebook/BTI/Deep/data/raw/9276014.json
/home/jovyan/notebook/BTI/Deep/data/raw/26656068.json
/home/jovyan/notebook/BTI/Deep/data/raw/18255165.json
/home/jovyan/notebook/BTI/Deep/data/raw/8495339.json
/home/jovyan/notebook/BTI/Deep/data/raw/22639386.json
/home/jovyan/notebook/BTI/Deep/data/raw/12507117.json
/home/jovyan/notebook/BTI/Deep/data/raw/1816562.json
/home/jovyan/notebook/BTI/Deep/data/raw/24835161.json
/home/jovyan/notebook/BTI/Deep/data/raw/27419109.json
/home/jovyan/notebook/BTI/Deep/data/raw/12962315.json
/home/jovyan/notebook/BTI/Deep/data/raw/11278709.json
/home/jovyan/notebook/BTI/Deep/data/raw/7674372.json
/home/jovyan/notebook/BTI/Deep/data/raw/16376103.json
/home/jovyan/notebook/BTI/Deep/data/raw/17765386.json
/home/jovyan/notebook/BTI/Deep/da

/home/jovyan/notebook/BTI/Deep/data/raw/27347040.json
/home/jovyan/notebook/BTI/Deep/data/raw/18599954.json
/home/jovyan/notebook/BTI/Deep/data/raw/10563216.json
/home/jovyan/notebook/BTI/Deep/data/raw/28612842.json
/home/jovyan/notebook/BTI/Deep/data/raw/26895770.json
/home/jovyan/notebook/BTI/Deep/data/raw/27132046.json
/home/jovyan/notebook/BTI/Deep/data/raw/25644393.json
/home/jovyan/notebook/BTI/Deep/data/raw/8495707.json
/home/jovyan/notebook/BTI/Deep/data/raw/28330876.json
/home/jovyan/notebook/BTI/Deep/data/raw/25362140.json
/home/jovyan/notebook/BTI/Deep/data/raw/14566211.json
/home/jovyan/notebook/BTI/Deep/data/raw/26208873.json
/home/jovyan/notebook/BTI/Deep/data/raw/23891111.json
/home/jovyan/notebook/BTI/Deep/data/raw/25735038.json
/home/jovyan/notebook/BTI/Deep/data/raw/16973299.json
/home/jovyan/notebook/BTI/Deep/data/raw/28797738.json
/home/jovyan/notebook/BTI/Deep/data/raw/7501282.json
/home/jovyan/notebook/BTI/Deep/data/raw/1674004.json
/home/jovyan/notebook/BTI/Deep/

/home/jovyan/notebook/BTI/Deep/data/raw/16650136.json
/home/jovyan/notebook/BTI/Deep/data/raw/22733568.json
/home/jovyan/notebook/BTI/Deep/data/raw/1226226.json
/home/jovyan/notebook/BTI/Deep/data/raw/26795580.json
/home/jovyan/notebook/BTI/Deep/data/raw/18023506.json
/home/jovyan/notebook/BTI/Deep/data/raw/3730584.json
/home/jovyan/notebook/BTI/Deep/data/raw/10556305.json
/home/jovyan/notebook/BTI/Deep/data/raw/16382189.json
/home/jovyan/notebook/BTI/Deep/data/raw/7861450.json
/home/jovyan/notebook/BTI/Deep/data/raw/8832592.json
/home/jovyan/notebook/BTI/Deep/data/raw/25448317.json
/home/jovyan/notebook/BTI/Deep/data/raw/21056635.json
/home/jovyan/notebook/BTI/Deep/data/raw/8084471.json
/home/jovyan/notebook/BTI/Deep/data/raw/21545645.json
/home/jovyan/notebook/BTI/Deep/data/raw/28951321.json
/home/jovyan/notebook/BTI/Deep/data/raw/25136404.json
/home/jovyan/notebook/BTI/Deep/data/raw/28218283.json
/home/jovyan/notebook/BTI/Deep/data/raw/8197301.json
/home/jovyan/notebook/BTI/Deep/dat

/home/jovyan/notebook/BTI/Deep/data/raw/22962604.json
/home/jovyan/notebook/BTI/Deep/data/raw/24361736.json
/home/jovyan/notebook/BTI/Deep/data/raw/18374306.json
/home/jovyan/notebook/BTI/Deep/data/raw/27844288.json
/home/jovyan/notebook/BTI/Deep/data/raw/29182615.json
/home/jovyan/notebook/BTI/Deep/data/raw/27483466.json
/home/jovyan/notebook/BTI/Deep/data/raw/10655101.json
/home/jovyan/notebook/BTI/Deep/data/raw/25781636.json
/home/jovyan/notebook/BTI/Deep/data/raw/489263.json
/home/jovyan/notebook/BTI/Deep/data/raw/26066722.json
/home/jovyan/notebook/BTI/Deep/data/raw/2601563.json
/home/jovyan/notebook/BTI/Deep/data/raw/9224525.json
/home/jovyan/notebook/BTI/Deep/data/raw/11594735.json
/home/jovyan/notebook/BTI/Deep/data/raw/25784209.json
/home/jovyan/notebook/BTI/Deep/data/raw/24121008.json
/home/jovyan/notebook/BTI/Deep/data/raw/2110844.json
/home/jovyan/notebook/BTI/Deep/data/raw/11823117.json
/home/jovyan/notebook/BTI/Deep/data/raw/15992375.json
/home/jovyan/notebook/BTI/Deep/da

...

/home/jovyan/notebook/BTI/Deep/data/raw/8971792.json
/home/jovyan/notebook/BTI/Deep/data/raw/23112793.json
/home/jovyan/notebook/BTI/Deep/data/raw/15020092.json
/home/jovyan/notebook/BTI/Deep/data/raw/9045075.json
/home/jovyan/notebook/BTI/Deep/data/raw/23962957.json
/home/jovyan/notebook/BTI/Deep/data/raw/25456433.json
/home/jovyan/notebook/BTI/Deep/data/raw/17723029.json
/home/jovyan/notebook/BTI/Deep/data/raw/19492440.json
/home/jovyan/notebook/BTI/Deep/data/raw/21269521.json
/home/jovyan/notebook/BTI/Deep/data/raw/22569158.json
/home/jovyan/notebook/BTI/Deep/data/raw/21186575.json
/home/jovyan/notebook/BTI/Deep/data/raw/17580438.json
/home/jovyan/notebook/BTI/Deep/data/raw/20804819.json
/home/jovyan/notebook/BTI/Deep/data/raw/21396384.json
/home/jovyan/notebook/BTI/Deep/data/raw/7895023.json
/home/jovyan/notebook/BTI/Deep/data/raw/16326117.json
/home/jovyan/notebook/BTI/Deep/data/raw/25447477.json
/home/jovyan/notebook/BTI/Deep/data/raw/18167452.json
/home/jovyan/notebook/BTI/Deep/

/home/jovyan/notebook/BTI/Deep/data/raw/28597477.json
/home/jovyan/notebook/BTI/Deep/data/raw/22785400.json
/home/jovyan/notebook/BTI/Deep/data/raw/24674862.json
/home/jovyan/notebook/BTI/Deep/data/raw/25769372.json
/home/jovyan/notebook/BTI/Deep/data/raw/1436386.json
/home/jovyan/notebook/BTI/Deep/data/raw/24040266.json
/home/jovyan/notebook/BTI/Deep/data/raw/17767510.json
/home/jovyan/notebook/BTI/Deep/data/raw/20546705.json
/home/jovyan/notebook/BTI/Deep/data/raw/26057360.json
/home/jovyan/notebook/BTI/Deep/data/raw/9147402.json
/home/jovyan/notebook/BTI/Deep/data/raw/23458672.json
/home/jovyan/notebook/BTI/Deep/data/raw/11673027.json
/home/jovyan/notebook/BTI/Deep/data/raw/8374918.json
/home/jovyan/notebook/BTI/Deep/data/raw/18420401.json
/home/jovyan/notebook/BTI/Deep/data/raw/12781786.json
/home/jovyan/notebook/BTI/Deep/data/raw/17451646.json
/home/jovyan/notebook/BTI/Deep/data/raw/28987626.json
/home/jovyan/notebook/BTI/Deep/data/raw/10397363.json
/home/jovyan/notebook/BTI/Deep/

/home/jovyan/notebook/BTI/Deep/data/raw/2723752.json
/home/jovyan/notebook/BTI/Deep/data/raw/18985107.json
/home/jovyan/notebook/BTI/Deep/data/raw/21928404.json
/home/jovyan/notebook/BTI/Deep/data/raw/2072294.json
/home/jovyan/notebook/BTI/Deep/data/raw/24331544.json
/home/jovyan/notebook/BTI/Deep/data/raw/16880827.json
/home/jovyan/notebook/BTI/Deep/data/raw/7489320.json
/home/jovyan/notebook/BTI/Deep/data/raw/24586766.json
/home/jovyan/notebook/BTI/Deep/data/raw/24898658.json
/home/jovyan/notebook/BTI/Deep/data/raw/15896499.json
/home/jovyan/notebook/BTI/Deep/data/raw/20018408.json
/home/jovyan/notebook/BTI/Deep/data/raw/8848108.json
/home/jovyan/notebook/BTI/Deep/data/raw/19016329.json
/home/jovyan/notebook/BTI/Deep/data/raw/21080411.json
/home/jovyan/notebook/BTI/Deep/data/raw/12890773.json
/home/jovyan/notebook/BTI/Deep/data/raw/20572199.json
/home/jovyan/notebook/BTI/Deep/data/raw/9878757.json
/home/jovyan/notebook/BTI/Deep/data/raw/16258230.json
/home/jovyan/notebook/BTI/Deep/da

/home/jovyan/notebook/BTI/Deep/data/raw/7576639.json
/home/jovyan/notebook/BTI/Deep/data/raw/6850332.json
/home/jovyan/notebook/BTI/Deep/data/raw/26281039.json
/home/jovyan/notebook/BTI/Deep/data/raw/26376217.json
/home/jovyan/notebook/BTI/Deep/data/raw/3145100.json
/home/jovyan/notebook/BTI/Deep/data/raw/25071488.json
/home/jovyan/notebook/BTI/Deep/data/raw/26074766.json
/home/jovyan/notebook/BTI/Deep/data/raw/23966708.json
/home/jovyan/notebook/BTI/Deep/data/raw/9762897.json
/home/jovyan/notebook/BTI/Deep/data/raw/18585369.json
/home/jovyan/notebook/BTI/Deep/data/raw/10213147.json
/home/jovyan/notebook/BTI/Deep/data/raw/27288932.json
/home/jovyan/notebook/BTI/Deep/data/raw/11531168.json
/home/jovyan/notebook/BTI/Deep/data/raw/22310556.json
/home/jovyan/notebook/BTI/Deep/data/raw/16382208.json
/home/jovyan/notebook/BTI/Deep/data/raw/18060012.json
/home/jovyan/notebook/BTI/Deep/data/raw/8768314.json
/home/jovyan/notebook/BTI/Deep/data/raw/25899094.json
/home/jovyan/notebook/BTI/Deep/da

/home/jovyan/notebook/BTI/Deep/data/raw/14720221.json
/home/jovyan/notebook/BTI/Deep/data/raw/2714832.json
/home/jovyan/notebook/BTI/Deep/data/raw/7781067.json
/home/jovyan/notebook/BTI/Deep/data/raw/18639532.json
/home/jovyan/notebook/BTI/Deep/data/raw/27013689.json
/home/jovyan/notebook/BTI/Deep/data/raw/16750349.json
/home/jovyan/notebook/BTI/Deep/data/raw/26828652.json
/home/jovyan/notebook/BTI/Deep/data/raw/6258750.json
/home/jovyan/notebook/BTI/Deep/data/raw/14502087.json
/home/jovyan/notebook/BTI/Deep/data/raw/18374170.json
/home/jovyan/notebook/BTI/Deep/data/raw/18793683.json
/home/jovyan/notebook/BTI/Deep/data/raw/26103635.json
/home/jovyan/notebook/BTI/Deep/data/raw/6707249.json
/home/jovyan/notebook/BTI/Deep/data/raw/10029236.json
/home/jovyan/notebook/BTI/Deep/data/raw/21573120.json
/home/jovyan/notebook/BTI/Deep/data/raw/29431797.json
/home/jovyan/notebook/BTI/Deep/data/raw/9765601.json
/home/jovyan/notebook/BTI/Deep/data/raw/26413472.json
/home/jovyan/notebook/BTI/Deep/da

In [102]:
scholar_dict = spy_querier.articles[0].__dict__['attrs']
for key in scholar_dict:
    jsonData['scholar_'+key] = scholar_dict[key]

In [109]:
jsonData

{'AB': 'The present data confirm the results of others that post-synaptic receptor changes may contribute to the decline in brain cholinergic function in ageing and dementia. We have also shown that chronic oral treatment with an extract of Gingko biloba increases the apparent muscarinic receptor population in the hippocampus of the aged Fisher 344 rat. The possible effect on (3H) kainic acid binding to the kainate-excitatory amino acid site is also interesting because of the proposed association of neurodegenerative disease and excessive excitatory amino neurotransmission.',
 'AU': ['Taylor JE'],
 'CRDT': ['1986/09/25 00:00'],
 'DCOM': '19870106',
 'DP': '1986 Sep 25',
 'EDAT': '1986/09/25 00:00',
 'FAU': ['Taylor, J E'],
 'IP': '31',
 'IS': '0755-4982 (Print) 0755-4982 (Linking)',
 'JID': '8302490',
 'JT': 'Presse medicale (Paris, France : 1983)',
 'LA': ['fre'],
 'LR': '20161209',
 'MH': ['Aging/drug effects',
  'Animals',
  'Brain/*drug effects/metabolism',
  'Male',
  'Neurotransm

In [78]:
with open(,'r') as raw_file:

    



    

    [print(href) for href in html_href];


    ['url_versions'][0]+'&num=100'

In [89]:
scholar_dict = spy_querier.articles[0].__dict__['attrs']

In [94]:
aux

{'scholar_cluster_id': ['1022953566400655269', 'Cluster ID', 5],
 'scholar_excerpt': ['Abstract The present data confirm the results of others that post-synaptic receptor changes may contribute to the decline in brain cholinergic function in ageing and dementia. We have also shown that chronic oral treatment with an extract of Gingko biloba increases the apparent muscarinic receptor population in the hippocampus of the aged Fisher 344 rat. The possible effect on (3H) kainic acid binding to the kainate-excitatory amino acid site is also interesting because of the proposed association of neurodegenerative disease and ',
  'Excerpt',
  10],
 'scholar_num_citations': [51, 'Citations', 3],
 'scholar_num_versions': [2, 'Versions', 4],
 'scholar_title': ['Neuromediator binding to receptors in the rat brain. The effect of chronic administration of Ginkgo biloba extract',
  'Title',
  0],
 'scholar_url': ['http://europepmc.org/abstract/med/2878427', 'URL', 1],
 'scholar_url_citation': [None, 'C

In [85]:
spy_querier.articles[0].__dict__['attrs']

{'cluster_id': ['1022953566400655269', 'Cluster ID', 5],
 'excerpt': ['Abstract The present data confirm the results of others that post-synaptic receptor changes may contribute to the decline in brain cholinergic function in ageing and dementia. We have also shown that chronic oral treatment with an extract of Gingko biloba increases the apparent muscarinic receptor population in the hippocampus of the aged Fisher 344 rat. The possible effect on (3H) kainic acid binding to the kainate-excitatory amino acid site is also interesting because of the proposed association of neurodegenerative disease and ',
  'Excerpt',
  10],
 'num_citations': [51, 'Citations', 3],
 'num_versions': [2, 'Versions', 4],
 'title': ['Neuromediator binding to receptors in the rat brain. The effect of chronic administration of Ginkgo biloba extract',
  'Title',
  0],
 'url': ['http://europepmc.org/abstract/med/2878427', 'URL', 1],
 'url_citation': [None, 'Citation link', 9],
 'url_citations': ['http://scholar.go

In [88]:
pdf_page

'http://scholar.google.com/scholar?cluster=1022953566400655269&hl=en&as_sdt=0,5&num=100'

In [57]:
raw_json['AU'][0]

'Taylor JE'

In [60]:
spy_querier.articles[0].__dict__

{'attrs': {'cluster_id': ['467996306782513994', 'Cluster ID', 5],
  'excerpt': ['This article surveys contemporary theories of international migration in order to illuminate their leading propositions, assumptions, and hypotheses. In doing so, it hopes to pave the way for a systematic empirical evaluation of their guiding tenets. The authors divide the ',
   'Excerpt',
   10],
  'num_citations': [5288, 'Citations', 3],
  'num_versions': [13, 'Versions', 4],
  'title': ['Theories of international migration: A review and appraisal',
   'Title',
   0],
  'url': ['http://www.jstor.org/stable/2938462', 'URL', 1],
  'url_citation': [None, 'Citation link', 9],
  'url_citations': ['http://scholar.google.com/scholar?cites=467996306782513994&as_sdt=2005&sciodt=0,5&hl=en',
   'Citations list',
   7],
  'url_pdf': [None, 'PDF link', 6],
  'url_versions': ['http://scholar.google.com/scholar?cluster=467996306782513994&hl=en&as_sdt=0,5',
   'Versions list',
   8],
  'year': ['1993', 'Year', 2]},
 'ci

In [52]:
pdf_page

'http://scholar.google.com/scholar?cluster=467996306782513994&hl=en&as_sdt=0,5&num=100'

In [48]:
title = raw_json['TI']
author = raw_json['AU'][0]
print(title)
print(author)

[Neuromediator binding to receptors in the rat brain. The effect of chronic administration of Ginkgo biloba extract].
Taylor JE


In [ ]:



author = 'Hinman JR'
title = 'Neural mechanisms of navigation involving interactions of cortical and subcortical structures.'

author = 'Hinman JR'
title = 'Neural mechanisms of navigation involving interactions of cortical and subcortical structures.'


author = "Kropff E"
title = 'Speed cells in the medial entorhinal cortex'

author = 'CA Gleaves'
title =  'Rapid detection of cytomegalovirus in MRC-5 cells inoculated with urine specimens by using low-speed centrifugation and monoclonal antibody to an early antigen.'

author = 'SP Palecek'
title = 'Integrin-ligand binding properties govern cell migration speed through cell-substratum adhesiveness'





pdf_page

import requests

html=''

for line in requests.get(pdf_page):
    html=html+str(line)
html_href = [href.replace("'b'","") for href in re.findall('href="(.*?)"',html)]
html_href = set([href for href in html_href if 'pdf' in href])

[print(href) for href in html_href];

In [24]:
corpus_keywords = ['spatial navigation','speed cells','grid cells','place cells','conjunctive cells']

In [27]:
for keyword in corpus_keywords:
    get_json(keyword)

29501041,29500808,29500717,29500537,29497677,29499309,29499275,29499274,29499176,29498748,29498005,29497904,29497903,29497366,29497296,29497131,29496988,29496987,29496644,29496632,29496611,29496151,29496139,29495896,29495532,29495433,29494891,29494862,29494861,29494759,29494605,29494490,29494196,29494185,29492815,29492757,29492616,29492510,29491219,29491011,29490666,29489273,29489229,29489163,29490264,29490235,29489588,29489460,29489454,29488894,29488843,29488342,29488277,29488138,29488136,29488134,29488099,29487522,29487509,29487503,29487370,29487336,29487299,29487212,29487124,29487122,29486870,29486864,29486768,29486296,29485243,29485232,29485116,29485078,29484897,29484772,29484405,29484389,29484271,29484264,29484252,29483660,29482365,29482345,29482048,29481885,29481858,29481784,29481768,29481626,29481319,29480936,29480581,29480413,29479505,29479305,29478968,29478916,29478897,29478873,29478713,29478199,29477596,29477585,29477415,29477301,29477029,29476982,29476948,29476913,29476822,2

29284679,29284109,29284046,29283314,29283042,29282816,29282556,29282124,29282044,29281967,29281813,29280418,29280246,29280245,29280034,29280004,29279390,29279367,29279309,29279308,29279051,29278888,29278101,29278027,29277983,29277879,29277710,29277652,29277582,29277490,29277371,29277066,29276735,29276487,29276476,29276473,29276216,29275839,29275796,29275328,29275206,29275185,29275163,29274883,29274882,29274875,29274751,29274741,29274503,29274430,29274351,29274291,29274095,29274031,29273784,29273398,29273230,29273062,29272548,29272468,29272467,29272297,29271834,29271637,29271291,29270773,29270738,29269412,29269405,29269276,29269268,29269262,29269186,29269074,29268976,29267967,29267958,29267792,29266926,29266595,29266510,29266459,29266170,29265830,29265681,29265673,29265092,29264962,29263406,29263397,29263361,29263233,29262336,29261743,29261717,29261664,29260931,29260547,29260492,29260372,29260371,29260367,29260163,29260016,29259854,29259353,29259151,29258870,29258847,29258552,29258546,2

29084578,29084550,29084334,29083204,29082469,29081887,29081745,29081740,29081424,29080744,29080717,29080716,29080714,29071065,29080472,29080453,29079799,29079688,29079533,29079430,29079294,29079140,29078397,29078387,29078334,29078046,29078045,29077793,29077553,29077163,29077077,29076975,29076667,29076435,29076268,29075579,29075577,29075536,29075513,29075179,29075178,29074877,29074463,29074416,29074343,29074292,29074125,29073650,29073644,29073641,29073081,29072798,29072793,29072005,29071973,29071954,29071896,29071893,29071234,29070884,29070854,29070790,29070752,29070630,29070471,29069820,29069807,29069596,29069591,29069555,29069083,29069042,29068596,29068054,29068027,29067809,29067448,29067447,29067352,29067330,29067327,



2000,29067322,29067314,29067112,29067000,29066956,29066955,29066953,29066948,29066946,29066900,29066839,29066556,29066369,29066368,29065344,29065291,29065194,29064783,29064725,29064675,29064447,29064341,29063964,29063831,29063591,29063330,29063319,29063211,29063112,29062800,29062688,29062097,29061703,29061639,29061584,29061526,29061366,29060939,29060837,29060609,29060534,29060514,29060316,29060312,29060217,29060053,29059927,29059594,29059309,29059301,29058763,29058455,29058357,29058356,29058349,29058184,29058179,29058042,29057768,29057721,29057696,29057631,29057625,29056913,29056904,29056525,29056362,29056359,29056296,29055675,29055260,29054882,29054611,29054591,29054542,29054451,29054431,29054430,29054390,29054286,29054014,29053824,29053799,29053778,29053699,29053689,29053682,29053191,29052615,29052243,29051381,29051084,29051075,29050859,29050390,29050205,29049383,29049070,29048465,29048371,29047291,29046888,29046883,29046699,29046426,29046349,29046322,29045497,29044813,29044802,29044

28648549,28648501,28648389,28648093,28647595,28647594,28647555,28647536,28647411,28647011,28646910,28646794,28646687,28646469,28646414,28646349,28646259,28645788,28645779,28645745,28645308,28645069,28644985,28644902,28644824,28644490,28643873,28643105,28642699,28642691,28642688,28642476,28642339,28642282,28642096,28642095,28642068,28641933,28641510,28641287,28641164,28641116,28641077,28640668,28640143,28639431,28638927,28638916,28638915,28638710,28638322,28637953,28637402,28637318,28637174,28636953,28636948,28636875,28636563,28634836,28634745,28634464,28634444,28634382,28634329,28634266,28634087,28633952,28633291,28633076,28633005,28632902,28632760,28632521,28632301,28632041,28631869,28631721,28631553,28631232,28630497,28630478,28630452,



...

4447563,4442479,4438558,4437728,4437726,4437124,4436683,4435041,4431840,4431838,4430761,4430760,4430737,4426285,4422320,4375047,4373680,4372566,4219190,4153783,4138771,4138770,4420173,4370916,4422276,4418683,4418171,4417044,4424843,4471677,4420821,4418713,4607251,4475430,4461116,4460919,4445274,4444856,4437746,4430929,4429745,4429522,4425996,4425196,4413122,4412177,4377913,4372986,4372323,4215528,4154738,4154114,4153688,4136701,4143026,4853717,4458916,4458913,4458909,4851746,4604978,4152793,4853159,4612567,4610593,4606882,4479792,4478618,4478329,4477079,4473750,4472950,4455162,4431821,4431567,4429533,4429514,4429512,4420388,4417083,4413134,4412651,4374523,4850389,4855028,4852569,4850525,4135929,4412501,4137683,4858286,4609109,4843258,4843256,4611547,4610612,4607007,4479893,4479820,4473462,4459114,4455497,4444763,4433762,4421891,4419236,4419197,4418718,4418698,4415656,4214341,4213659,4213408,4374717,4858320,4836627,4854703,4841165,4152613,4859352,4848448,4834210,4607005,4606878,4606389,

2000,4274161,4268525,4265282,4220182,4220181,4210922,4209586,4204787,4204167,4199908,4199907,4198039,4197865,4127192,4125767,4121630,4118435,4645204,4630226,4654225,4663626,4655405,4655402,4655397,4652626,4650341,4649759,4630971,4541487,4265745,4145161,4127071,4117334,4641264,4641263,4345032,4638923,4673788,4635363,4629216,5086248,5084445,4679422,4676617,4673562,4663323,4663317,4663314,4663306,4663303,4663301,4655719,4654529,4651793,4646805,4643289,4570176,4268066,4197225,4634323,4634322,4507808,5087061,4631757,5075345,4342404,5076641,5074302,5074301,5073889,5056927,4678854,4678852,4672900,4672267,4652358,4649990,4627786,4600348,4599682,4599677,4599675,4561911,4403616,4209279,4341126,5056975,5054641,5080492,5073779,5072388,5071901,5068854,5064894,5054511,5050899,4673376,4668755,4667105,4667103,4658583,4658581,4658579,4653787,4653748,4652004,4652003,4652001,4648390,4644329,4638365,4637923,4634664,4628387,4628086,4405632,4403688,4403687,4354985,4354433,4354432,4346936,4341978,4341964,411

2000,5970759,5970676,5970447,5927906,5923482,5922048,5332832,4958844,4162476,5969326,5969325,5940897,5987613,5968260,5967372,5950056,5911842,5911102,5329618,6010347,6009978,6007733,6005557,5999189,5967909,5967675,5967661,5963381,5956463,5947925,5947924,5939733,5937496,5925222,5925221,5924723,5333010,4380692,4165377,4165363,5336214,5336213,5914886,6007669,6003450,6003449,5961963,5939044,5939041,5938141,5938130,4957337,5942259,6005513,6004315,5963314,5961912,5222082,4143685,6007250,6007249,5949684,5927272,5927271,5909294,5906465,4381352,5931222,5956510,5959942,6005218,5955959,5942816,5939991,5939564,5937257,5917813,5911302,5910903,5219757,4957290,4383163,5936150,5903272,5903271,5220953,4159915,5948540,4961113,6014831,6008552,6005628,5987163,5984361,5983986,5983207,5982855,5982710,5974485,5974096,5973994,5973099,5965959,5962236,5959506,5958502,5958265,5958238,5955968,5954303,5939645,5924892,5920552,5920551,5917287,5910705,5903302,5334004,5331850,5298021,5233565,5233560,4989024,4876369,486

815,29491968,29478701,29467633,29467145,29461983,29449458,29449457,29442559,29427284,29424434,29414071,29407275,29405653,29404551,29380269,29374553,29364869,29358117,29335778,29335356,29327266,29311746,29287744,29270109,29237555,29230062,29209230,29208224,29203335,29199073,29187558,29185381,29181629,29175306,29170645,29165083,29163085,29159664,29158177,29133436,29130062,29130061,29130060,29122592,29113794,29089924,29088300,29085184,29078334,29073650,29071993,29071352,29067352,29053781,29044802,29042687,29030432,29026510,28979196,28931613,28930523,28893579,28892088,28890919,28888032,28874742,28869583,28867995,28866680,28866679,28866677,28858613,28826483,28824390,28818696,28787026,28785214,28780430,28778443,28775698,28770385,28764713,28760858,28760627,28752318,28751148,28744722,28736170,28726502,28720550,28720024,28710800,28698637,28697363,28696588,28686374,28684296,28675149,28663090,28661173,28660347,28632038,28628647,28628104,28624709,28609014,28602659,28602491,28600742,28597846,285906

11,29465399,29443106,29442559,29432886,29386397,29386260,29382754,29371658,29367838,29361651,29339345,29335607,29333481,29311746,29309406,29276476,29230055,29230051,29218403,29213234,29196525,29190508,29176562,29153321,29109512,29087942,29075993,29073644,29056296,29037492,28968386,28967910,28965758,28958464,28915518,28890051,28888183,28887226,28858613,28842863,28832719,28829435,28824388,28814638,28787605,28785214,28769779,28768062,28767687,28756950,28750005,28724433,28708881,28703324,28701481,28678438,28675670,28640608,28628647,28628104,28624709,28599195,28590682,28591796,28533968,28515661,28511360,28494861,28467409,28454032,28450227,28424398,28418593,28396399,28392071,28371135,28370671,28358077,28343867,28334610,28334142,28314046,28270783,28199875,28178279,28161726,28111080,28085304,28084992,28067005,28034697,28025983,28001122,27943643,27941523,27940253,27936209,27932929,27870120,27841548,27829799,27113083,27770476,27792892,27792723,27765433,27764662,27764597,27097603,27756084,2767793

In [7]:
record

{'AB': 'The effect of environmental enrichment on normal rats, rats that received hemidecortication at birth, and rats that received hemidecortication when adult was studied in the Morris water task, which is a spatial navigation task requiring the use of distal cues for successful performance. Enrichment was achieved by housing the rats for 90 days in a large outdoor compound that was designed to model a natural environment. Adult hemidecorticated lab-raised rats were severely impaired in the acquisition of the task but neonatally hemidecorticated rats, although also impaired, showed significant sparing. Postsurgical, but not presurgical, enrichment of adult hemidecorticated rats significantly enhanced their recovery. Enrichment had little effect on neonatally decorticated rats or on normal rats. Although there were no gross anatomical changes associated with enrichment, the paradigm provides both a robust phenomena and a cortically dependent task that is ideal for investigating the p

In [ ]:

json.dumps(your_data, ensure_ascii=False)

term='"speed cells"'

from Bio import Entrez,Medline

Entrez.email = 'dr.publico88@gmail.com'


with Entrez.egquery(term=term) as handle:
    record       = Entrez.read(handle)
    record_count = int(''.join([entry['Count'] for entry in record['eGQueryResult'] if entry['DbName']=='pubmed']))

with Entrez.esearch(db="pubmed", term=term, retmax=record_count) as handle:
    record = Entrez.read(handle)
    idlist = record["IdList"]

record_list = []
with Entrez.efetch(db="pubmed", id=idlist, rettype="medline", retmode="text") as handle:
    for record in Medline.parse(handle):
        record_list.append(record)
        print(record['TI'])

lista = get_pmid()

c = 0;
for record in record_list:
    if 'AID' in record:
        c = c + 1;
        print(record['AU'][0])
        print(record['TI'])

import sys
sys.path.insert(0, './scholar.py')
import scholar as spy

spy_settings = spy.ScholarSettings()
spy_settings.citform = spy_settings.CITFORM_BIBTEX;
spy_settings.results = 10;

spy_querier = spy.ScholarQuerier()
spy_querier.apply_settings(spy_settings)


author = 'Hinman JR'
title = 'Neural mechanisms of navigation involving interactions of cortical and subcortical structures.'

spy_query = spy.SearchScholarQuery()
spy_query.set_author(author)
spy_query.set_phrase(title)

spy_querier.send_query(spy_query)

for article in spy_querier.articles:
    for key in article:
        print(key,article[key])

spy_querier.articles[0].attrs

handle = Entrez.esearch(db="pubmed", term=term, retmax=record_count)
Medline.read(handle)

handle = Entrez.efetch(db='pubmed', id=pmid, retmode='text', rettype='abstract')


print_abstract(idlist)

def print_abstract(pmid):
    handle = Entrez.efetch(db='pubmed', id=pmid, retmode='text', rettype='abstract')
    print(handle.read())